<a href="https://colab.research.google.com/github/JavierBescosArtigas/MBID08Visualization-GuidedActies/blob/main/MBID08PlotlyJavierBescos.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

En este cuaderno se ha realizado toda la limpieza de datos así como una gran cantidad de las representaciones usadas para el **trabajo de la asignatura MBID08 Visualización de Datos (2022)** por parte de Javier Bescós.

* Para mi propia reutilización de partes de código, todas las subsecciones hasta **Ver las figuras interactivamente [...]** corresponden al código

* Para observar únicamente los gráficos de forma interactiva en el cuaderno, están todos reunidos en la última sección. Simplemente ejecutar el código de las secciones anteriores 'como una caja negra' 

# ¿Vivimos en 1 mundo más violento?
* Macro ~ parece que si, o que no, o que estamos a merced de otros
* Micro ~ muertes violentas, se trabajará con excel para el scrapping en [link](https://datosmacro.expansion.com/) y datawraper para alguna representación
--> [link](https://datos.bancomundial.org/indicador/VC.IHR.PSRC.P5?view=chart)


### imports y carga de datasets.



In [ ]:
!pip install pycountry_convert > /dev/null #pycountry, fundamental para la limpieza de datos. Tarda 1 min en instalarse
import plotly.express as px
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pycountry_convert as pc
import ipywidgets as widgets
import plotly.graph_objects as go

In [ ]:
!wget https://api.worldbank.org/v2/es/indicator/MS.MIL.XPND.GD.ZS?downloadformat=csv
!unzip /content/MS.MIL.XPND.GD.ZS?downloadformat=csv

!head -n 5 /content/API_MS.MIL.XPND.GD.ZS_DS2_es_csv_v2_4523928.csv

--2022-11-24 11:04:47--  https://api.worldbank.org/v2/es/indicator/MS.MIL.XPND.GD.ZS?downloadformat=csv
Resolving api.worldbank.org (api.worldbank.org)... 52.188.136.184
Connecting to api.worldbank.org (api.worldbank.org)|52.188.136.184|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 93548 (91K) [application/zip]
Saving to: ‘MS.MIL.XPND.GD.ZS?downloadformat=csv’

MS.MIL.XPND.GD.ZS?d 100%[===================>]  91.36K  --.-KB/s    in 0.03s   

2022-11-24 11:04:48 (2.81 MB/s) - ‘MS.MIL.XPND.GD.ZS?downloadformat=csv’ saved [93548/93548]

Archive:  /content/MS.MIL.XPND.GD.ZS?downloadformat=csv
  inflating: Metadata_Indicator_API_MS.MIL.XPND.GD.ZS_DS2_es_csv_v2_4523928.csv  
  inflating: API_MS.MIL.XPND.GD.ZS_DS2_es_csv_v2_4523928.csv  
  inflating: Metadata_Country_API_MS.MIL.XPND.GD.ZS_DS2_es_csv_v2_4523928.csv  
﻿"Data Source","Indicadores del desarrollo mundial",

"Last Updated Date","2022-09-16",

"Country Name","Country Code","Indicator Name","Indicator Code"

In [ ]:
gastoMilitar = pd.read_csv("/content/API_MS.MIL.XPND.GD.ZS_DS2_es_csv_v2_4523928.csv", skiprows = 4) #% del pib

gastoMilitar = gastoMilitar.drop(columns = ['Unnamed: 66',])

#nueva columna
gastoMilitar=gastoMilitar.assign(Continente = 1) 
def getContinents(x):
  #from alphacode3 in dataframe to continent
    try:
        return  pc.convert_continent_code_to_continent_name(pc.country_alpha2_to_continent_code(pc.country_alpha3_to_country_alpha2(x)) )
    except:
        return 'Undetermined'
gastoMilitar.Continente = gastoMilitar["Country Code"].apply(getContinents)

gastoMilitar = gastoMilitar.drop(gastoMilitar[gastoMilitar['Continente'] == 'Undetermined'].index )

gastoMilitar = gastoMilitar.melt(id_vars=['Country Name', 'Country Code', 'Indicator Name', 'Indicator Code', 'Continente'], var_name='Año').sort_values(['Country Name', 'Año', 'Continente'])
gastoMilitar.rename(columns = {"value": "GastoMilitar%"}, inplace = True)
#NAS with fill foward by country

gastoMilitar['GastoMilitar%'] = gastoMilitar.groupby('Country Name')['GastoMilitar%'].ffill()#ffoward

#gastoMilitar['GastoMilitar%'] = gastoMilitar.groupby('Country Name')['GastoMilitar%'].bfill()#fbackward, apply if necesary.


display(gastoMilitar[gastoMilitar['GastoMilitar%'].isna()]['GastoMilitar%'].count() , gastoMilitar['GastoMilitar%'].count())
#display(gastoMilitar.isnull().sum()) #nº de nulls

0

8004

### Plot 1 Gasto en defensa sobre porcentaje del PIB desde 1960 separado por 6 continentes


In [ ]:
fig1 = px.line(gastoMilitar, x="Año", y="GastoMilitar%", color="Country Name", line_group="Country Name", hover_name="Country Name",
        line_shape="spline", render_mode="svg",facet_col="Continente", range_y=[1,80], title="Gasto en defensa como porcentaje del PIB desde 1960 hasta 2020, separado por continentes",
         labels={
                     "GastoMilitar%": "Gasto Militar % sobre PIB",
                     "Country Name": "Seleccione país de la lista para ocultar/focalizar",
                    "Año": ''
                     
                 },
        )
fig1.update_layout(showlegend=True)
fig1.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1000)

fig1.show()

## Imports y carga dataset 2

In [ ]:
#!unzip /content/drive/MyDrive/MBID/militaryExpenditureDatosBancoMundial.zip #leer del drive, innecesario
!wget https://api.worldbank.org/v2/es/indicator/MS.MIL.XPND.CD?downloadformat=csv
!unzip /content/MS.MIL.XPND.CD?downloadformat=csv
!head -n5 /content/API_MS.MIL.XPND.CD_DS2_es_csv_v2_4541472.csv

--2022-11-24 11:05:54--  https://api.worldbank.org/v2/es/indicator/MS.MIL.XPND.CD?downloadformat=csv
Resolving api.worldbank.org (api.worldbank.org)... 52.188.136.184
Connecting to api.worldbank.org (api.worldbank.org)|52.188.136.184|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 94142 (92K) [application/zip]
Saving to: ‘MS.MIL.XPND.CD?downloadformat=csv.1’

MS.MIL.XPND.CD?down 100%[===================>]  91.94K  --.-KB/s    in 0.03s   

2022-11-24 11:05:55 (2.83 MB/s) - ‘MS.MIL.XPND.CD?downloadformat=csv.1’ saved [94142/94142]

Archive:  /content/MS.MIL.XPND.CD?downloadformat=csv
replace Metadata_Indicator_API_MS.MIL.XPND.CD_DS2_es_csv_v2_4541472.csv? [y]es, [n]o, [A]ll, [N]one, [r]ename: N
﻿"Data Source","Indicadores del desarrollo mundial",

"Last Updated Date","2022-09-16",

"Country Name","Country Code","Indicator Name","Indicator Code","1960","1961","1962","1963","1964","1965","1966","1967","1968","1969","1970","1971","1972","1973","1974","1975","1976",

In [ ]:
gastoMilitarAbsoluto = pd.read_csv("/content/API_MS.MIL.XPND.CD_DS2_es_csv_v2_4541472.csv", skiprows = 4)
gastoMilitarAbsoluto = gastoMilitarAbsoluto.drop(columns = ['Unnamed: 66',])

#nueva columna para homogeneizar qué paises eliminamos
gastoMilitarAbsoluto=gastoMilitarAbsoluto.assign(Continente = 1)

gastoMilitarAbsoluto.Continente = gastoMilitarAbsoluto["Country Code"].apply(getContinents)
gastoMilitarAbsoluto = gastoMilitarAbsoluto.drop(gastoMilitarAbsoluto[gastoMilitarAbsoluto['Continente'] == 'Undetermined'].index )

gastoMilitarAbsoluto = gastoMilitarAbsoluto.melt(id_vars=['Country Name', 'Country Code', 'Indicator Name', 'Indicator Code', 'Continente'], var_name='Año').sort_values(['Country Name', 'Año', 'Continente'])
gastoMilitarAbsoluto.rename(columns = {"value": "GastoMilitarTotal"}, inplace = True)
gastoMilitarAbsoluto['GastoMilitarTotal'] = gastoMilitarAbsoluto.groupby('Country Name')['GastoMilitarTotal'].ffill()#ffoward

gastoMilitarAbsoluto.Continente.unique()
gastoMilitarAbsoluto.columns

Index(['Country Name', 'Country Code', 'Indicator Name', 'Indicator Code',
       'Continente', 'Año', 'GastoMilitarTotal'],
      dtype='object')

### Plot 2, Gasto en defensa absoluto (USD) desde 1960 separado por continentes

In [ ]:
fig2 = px.line(gastoMilitarAbsoluto, x="Año", y="GastoMilitarTotal", color="Country Name", line_group="Country Name", hover_name="Country Name",
        line_shape="spline", render_mode="svg",facet_col="Continente", title="Gasto en defensa absoluto (USD) desde 1960 hasta 2020, separado por continentes.", range_y=[1,250000000000],
        labels={
                     "GastoMilitarTotal": "Gasto Militar Total (USD)",
                     "Country Name": "Seleccione país de la lista para ocultar/focalizar",
                     'Año' : '',
                     'Continente=': ''
                 }, 
        )
fig2.update_layout(showlegend=True)
fig2.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1000)
fig2.show()


## Vemos que sólo unos pocos agentes internacionales gastan la inmensa mayoría, del gasto. Veámoslo más en detalle.

In [ ]:
top15absoluto2020 = gastoMilitarAbsoluto[gastoMilitarAbsoluto['Año'] == '2020']
listaTop15 = list(top15absoluto2020.nlargest(15, ['GastoMilitarTotal'])['Country Name'])
#este diccionario acompañado de la función siguiente nos permitirá etiquetar todos los dataframes para quedarnos con los 15 países más importantes en 2020 ¡pero desde 1960!
dictOrdenDeseado = {}
for i in range(len(listaTop15)):
 dictOrdenDeseado[listaTop15[i]] = i
print(dictOrdenDeseado)
def ObtainOrdenDeseado(x):
  try:
    return(dictOrdenDeseado[x])
  except:
    return -1

#nueva columna
top15absoluto2020 = gastoMilitarAbsoluto.assign(top15_2020 = 0) 
top15absoluto2020['top15_2020'] = top15absoluto2020['Country Name'].apply(ObtainOrdenDeseado)#aquí se toman todos los años

NoTop15absoluto2020 = top15absoluto2020[top15absoluto2020['top15_2020'] == -1  ] #para plot futuro

top15absoluto2020 = top15absoluto2020[top15absoluto2020['top15_2020'] > -1  ]
top15absoluto2020.head(3)


{'Estados Unidos': 0, 'China': 1, 'India': 2, 'Federación de Rusia': 3, 'Reino Unido': 4, 'Arabia Saudita': 5, 'Alemania': 6, 'Francia': 7, 'Japón': 8, 'Corea, República de': 9, 'Italia': 10, 'Australia': 11, 'Emiratos Árabes Unidos': 12, 'Canadá': 13, 'Israel': 14}


Country Name Country Code                      Indicator Name  \
49       Alemania          DEU  Military expenditure (current USD)   
262      Alemania          DEU  Military expenditure (current USD)   
475      Alemania          DEU  Military expenditure (current USD)   
688      Alemania          DEU  Military expenditure (current USD)   
901      Alemania          DEU  Military expenditure (current USD)   
1114     Alemania          DEU  Military expenditure (current USD)   
1327     Alemania          DEU  Military expenditure (current USD)   
1540     Alemania          DEU  Military expenditure (current USD)   
1753     Alemania          DEU  Military expenditure (current USD)   
1966     Alemania          DEU  Military expenditure (current USD)   
2179     Alemania          DEU  Military expenditure (current USD)   
2392     Alemania          DEU  Military expenditure (current USD)   
2605     Alemania          DEU  Military expenditure (current USD)   
2818     Alemania          DEU  Military expenditure (current USD)   
3031     Alemania          DEU  Military expenditure (current USD)   
3244     Alemania          DEU  Military expenditure (current USD)   
3457     Alemania          DEU  Military expenditure (current USD)   
3670     Alemania          DEU  Military expenditure (current USD)   
3883     Alemania          DEU  Military expenditure (current USD)   
4096     Alemania          DEU  Military expenditure (current USD)   

      Indicator Code Continente   Año  GastoMilitarTotal  top15_2020  
49    MS.MIL.XPND.CD     Europe  1960       2.715197e+09           6  
262   MS.MIL.XPND.CD     Europe  1961       3.074753e+09           6  
475   MS.MIL.XPND.CD     Europe  1962       4.055355e+09           6  
688   MS.MIL.XPND.CD     Europe  1963       4.688620e+09           6  
901   MS.MIL.XPND.CD     Europe  1964       4.601310e+09           6  
1114  MS.MIL.XPND.CD     Europe  1965       4.686319e+09           6  
1327  MS.MIL.XPND.CD     Europe  1966       4.766403e+09           6  
1540  MS.MIL.XPND.CD     Europe  1967       5.037954e+09           6  
1753  MS.MIL.XPND.CD     Europe  1968       4.544109e+09           6  
1966  MS.MIL.XPND.CD     Europe  1969       5.150519e+09           6  
2179  MS.MIL.XPND.CD     Europe  1970       5.805254e+09           6  
2392  MS.MIL.XPND.CD     Europe  1971       6.829978e+09           6  
2605  MS.MIL.XPND.CD     Europe  1972       8.478071e+09           6  
2818  MS.MIL.XPND.CD     Europe  1973       1.123790e+10           6  
3031  MS.MIL.XPND.CD     Europe  1974       1.296520e+10           6  
3244  MS.MIL.XPND.CD     Europe  1975       1.438144e+10           6  
3457  MS.MIL.XPND.CD     Europe  1976       1.454982e+10           6  
3670  MS.MIL.XPND.CD     Europe  1977       1.628888e+10           6  
3883  MS.MIL.XPND.CD     Europe  1978       2.015979e+10           6  
4096  MS.MIL.XPND.CD     Europe  1979       2.332313e+10           6

### Plot 3 Top 15 agentes del 2020, ver su desarrollo histórico
...pero eso es otra historia

In [ ]:
fig3 = px.bar(top15absoluto2020 ,x="Country Name",y="GastoMilitarTotal",color="Continente",animation_group="Country Name",animation_frame="Año" , range_y=[60000000,top15absoluto2020.GastoMilitarTotal.max()*0.5],
              title="Siguiendo el desarrollo histórico de los 15 agentes internacionales más influyentes de la actualidad, desde 1960.",
              labels={
                     "GastoMilitarTotal": "Gasto Militar Total (USD)",
                     "Country Name": "",
                 }
              )
fig3.update_layout(transition = {'duration': 1000})
fig3.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1000)
fig3.show()

## Bueno, y cómo va el resto, no juegan al juego este o qué?

In [ ]:
NoTop15absoluto2020 = NoTop15absoluto2020[NoTop15absoluto2020['Año'] == '2020']
NoTop15absoluto2020 = NoTop15absoluto2020.dropna()
NoTop15absoluto2020.head(3)

Country Name Country Code                      Indicator Name  \
12781   Afganistán          AFG  Military expenditure (current USD)   
12783      Albania          ALB  Military expenditure (current USD)   
12782       Angola          AGO  Military expenditure (current USD)   

       Indicator Code Continente   Año  GastoMilitarTotal  top15_2020  
12781  MS.MIL.XPND.CD       Asia  2020       2.795770e+08          -1  
12783  MS.MIL.XPND.CD     Europe  2020       2.220227e+08          -1  
12782  MS.MIL.XPND.CD     Africa  2020       9.935944e+08          -1

### Plot 4 ¿Cómo se distribuye el resto de países, quitando a los gigantes, son una balsa de aceite, todos iguales ó podemos ver algo a partir de este indicador macro-económico?

In [ ]:
def plotTochoWidget(scopee = 'world', proyeccion = 'times'): #  ['africa', 'asia', 'europe', 'north america', 'south america', 'usa', 'world']
  
  fig4 = go.Figure(go.Choropleth(
      locations = NoTop15absoluto2020['Country Code'],
      locationmode = "ISO-3",
      z = NoTop15absoluto2020['GastoMilitarTotal'],
      text = NoTop15absoluto2020['Country Name'],
      colorscale = 'rainbow',  
    
      reversescale=False,
      marker_line_color='#efefef',
      marker_line_width=0.5,
      
      colorbar_title = 'Gasto Militar (USD)',
      )
  )
  
  # Establecemos las características del título y la apariencia del mapa base
  fig4.update_layout(
      title_text = 'Gasto Militar Absoluto (USD) para el año 2020, ignorando las 15 potencias armamentísticas más influyentes.',
      showlegend = True,
      geo = dict(
          scope= scopee , #AQUÍ ESTÁ LA MAGIA
          resolution=50,
          #projection_type = 'orthographic',  
          projection_type= proyeccion, # AQUÍ ESTÁ LA MAGIAx2
          showcoastlines=True, coastlinecolor="Black", 
          showocean=True,
          showcountries=True,
          oceancolor="LightBlue",  
          lakecolor="Blue",
          showland=True, landcolor="white",
          #tamaño imagen
            )
      )
  
  fig4.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1000)
  
  fig4.show()

#import ipywidgets as widgets
widgets.interact(plotTochoWidget, scopee = ['africa', 'asia', 'europe', 'north america', 'south america', 'world'], proyeccion = ['orthographic', 'times'] )# ['natural earth', 'miller', 'orthographic', 'times', 'airy'])


interactive(children=(Dropdown(description='scopee', index=5, options=('africa', 'asia', 'europe', 'north amer…

<function __main__.plotTochoWidget(scopee='world', proyeccion='times')>

### Plot 5~extra, mapa mundi con todos los países

In [ ]:
#gráfico extra con todos juntos, al verlo se entiende por qué no se incorpora como principal
fig5 = go.Figure(go.Choropleth(
      locations = gastoMilitarAbsoluto['Country Code'],
      locationmode = "ISO-3",
      z = NoTop15absoluto2020['GastoMilitarTotal'],
      text = NoTop15absoluto2020['Country Name'],
      colorscale = 'reds',  
    
      reversescale=False,
      marker_line_color='#efefef',
      marker_line_width=0.5,
      
      colorbar_title = 'Gasto Militar (USD)',
      )
  )
  
# Establecemos las características del título y la apariencia del mapa base
fig5.update_layout(
    title_text = 'Gasto Militar Absoluto (USD), 2020.',
    showlegend = True,
    geo = dict(
        scope= 'world' , 
        resolution=50,
        #projection_type = 'orthographic',  
        projection_type= 'orthographic', 
        showcoastlines=True, coastlinecolor="Black", 
        showocean=True,
        showcountries=True,
        oceancolor="LightBlue",  
        lakecolor="Blue",
        showland=True, landcolor="white",
        #tamaño imagen
          )
    )

fig5.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 900)

fig5.show()

# Parte 2: Análisis de datos de homicidios intencionados.

In [ ]:
#funcion get columna continente y limpia paises sin sentido (que no formen parte del diccionario country_alpha2 ó 3 de pc library)
def getColumnaContinente(df):
  df=df.assign(Continente = 1) 
  def getContinents(x):
    #from alphacode3 in dataframe
      try:
          return  pc.convert_continent_code_to_continent_name(pc.country_alpha2_to_continent_code(pc.country_alpha3_to_country_alpha2(x)) )
      except:
          return 'Undetermined'
  df.Continente = df["Country Code"].apply(getContinents)
  df = df.drop(df[df['Continente'] == 'Undetermined'].index )
  return df

In [ ]:
!wget https://api.worldbank.org/v2/es/indicator/SP.POP.TOTL?downloadformat=csv >/dev/null #poblacion por pais
!unzip SP.POP.TOTL?downloadformat=csv >/dev/null
!!head -n5 API_SP.POP.TOTL_DS2_es_csv_v2_4682121.csv 
#!rm *=csv*

--2022-11-24 11:07:27--  https://api.worldbank.org/v2/es/indicator/SP.POP.TOTL?downloadformat=csv
Resolving api.worldbank.org (api.worldbank.org)... 52.188.136.184
Connecting to api.worldbank.org (api.worldbank.org)|52.188.136.184|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 80377 (78K) [application/zip]
Saving to: ‘SP.POP.TOTL?downloadformat=csv’

SP.POP.TOTL?downloa 100%[===================>]  78.49K  --.-KB/s    in 0.03s   

2022-11-24 11:07:28 (2.51 MB/s) - ‘SP.POP.TOTL?downloadformat=csv’ saved [80377/80377]



['\ufeff"Data Source","Indicadores del desarrollo mundial",',
 '',
 '"Last Updated Date","2022-09-16",',
 '',
 '"Country Name","Country Code","Indicator Name","Indicator Code","1960","1961","1962","1963","1964","1965","1966","1967","1968","1969","1970","1971","1972","1973","1974","1975","1976","1977","1978","1979","1980","1981","1982","1983","1984","1985","1986","1987","1988","1989","1990","1991","1992","1993","1994","1995","1996","1997","1998","1999","2000","2001","2002","2003","2004","2005","2006","2007","2008","2009","2010","2011","2012","2013","2014","2015","2016","2017","2018","2019","2020","2021",']

In [ ]:
poblacionMundial = pd.read_csv("/content/API_SP.POP.TOTL_DS2_es_csv_v2_4682121.csv", skiprows = 4) # sobre 100 000 habitantes
poblacionMundial.drop(columns = 'Unnamed: 66', inplace = True)
poblacionMundial.columns
poblacionMundial = poblacionMundial[['Country Name', 'Country Code',
       '1960', '1961', '1962', '1963', '1964', '1965', '1966', '1967', '1968',
       '1969', '1970', '1971', '1972', '1973', '1974', '1975', '1976', '1977',
       '1978', '1979', '1980', '1981', '1982', '1983', '1984', '1985', '1986',
       '1987', '1988', '1989', '1990', '1991', '1992', '1993', '1994', '1995',
       '1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004',
       '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013',
       '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021'] ]
poblacionMundial = poblacionMundial.melt(id_vars = ['Country Name', 'Country Code'], value_name = 'population', var_name = 'Año')
poblacionMundial = getColumnaContinente(poblacionMundial)
#ffoward por pais
poblacionMundial['population'] = poblacionMundial.groupby('Country Name')['population'].ffill()

# nº nas
poblacionMundial.population.isna().sum()

30

In [ ]:
!wget https://api.worldbank.org/v2/es/indicator/VC.IHR.PSRC.P5?downloadformat=csv >/dev/null # homicidios intencionados
!unzip /content/VC.IHR.PSRC.P5?downloadformat=csv >/dev/null
!head -n5 API_VC.IHR.PSRC.P5_DS2_es_csv_v2_4499705.csv

--2022-11-24 11:07:28--  https://api.worldbank.org/v2/es/indicator/VC.IHR.PSRC.P5?downloadformat=csv
Resolving api.worldbank.org (api.worldbank.org)... 52.188.136.184
Connecting to api.worldbank.org (api.worldbank.org)|52.188.136.184|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 44776 (44K) [application/zip]
Saving to: ‘VC.IHR.PSRC.P5?downloadformat=csv’

VC.IHR.PSRC.P5?down 100%[===================>]  43.73K  --.-KB/s    in 0.03s   

2022-11-24 11:07:28 (1.45 MB/s) - ‘VC.IHR.PSRC.P5?downloadformat=csv’ saved [44776/44776]

﻿"Data Source","Indicadores del desarrollo mundial",

"Last Updated Date","2022-09-15",

"Country Name","Country Code","Indicator Name","Indicator Code","1960","1961","1962","1963","1964","1965","1966","1967","1968","1969","1970","1971","1972","1973","1974","1975","1976","1977","1978","1979","1980","1981","1982","1983","1984","1985","1986","1987","1988","1989","1990","1991","1992","1993","1994","1995","1996","1997","1998","1999","2000","2

In [ ]:
homicidiosIntencionados = pd.read_csv("/content/API_VC.IHR.PSRC.P5_DS2_es_csv_v2_4499705.csv", skiprows = 4) # sobre 100 000 habitantes
homicidiosIntencionados.drop(columns = 'Unnamed: 66', inplace = True)
# the melting
homicidiosIntencionados.columns
homicidiosIntencionados = homicidiosIntencionados.melt(id_vars = ['Country Name', 'Country Code', 'Indicator Name', 'Indicator Code'], value_name = 'HomicidiosPor100000', var_name = 'Año')

homicidiosIntencionados = getColumnaContinente(homicidiosIntencionados)
#ffoward por pais
homicidiosIntencionados['HomicidiosPor100000'] = homicidiosIntencionados.groupby('Country Name')['HomicidiosPor100000'].ffill()
#unir 2 datasets: poblacion y asesinatos
homicidiosIntencionados = homicidiosIntencionados.assign(Población = 1) 
homicidiosIntencionados.Población = poblacionMundial.population
homicidiosIntencionados.head()

#homicidios totales por año en un pais = (homicidios/100000 habts) * nº habitantes/100000
homicidiosIntencionados = homicidiosIntencionados.assign(HomicidiosTotalesAnual = 1) 
homicidiosIntencionados.HomicidiosTotalesAnual = homicidiosIntencionados['HomicidiosPor100000'] * homicidiosIntencionados['Población'] / 100000
#ffoward por pais
homicidiosIntencionados['HomicidiosTotalesAnual'] = homicidiosIntencionados.groupby('Country Name')['HomicidiosTotalesAnual'].ffill()

#nº nas
homicidiosIntencionados.HomicidiosTotalesAnual.isna().sum()

8264

In [ ]:
homicidiosIntencionados.head(3)

Country Name Country Code  \
0        Aruba          ABW   
2   Afganistán          AFG   
4       Angola          AGO   

                                      Indicator Name  Indicator Code   Año  \
0  Homicidios intencionales (por cada 100.000 hab...  VC.IHR.PSRC.P5  1960   
2  Homicidios intencionales (por cada 100.000 hab...  VC.IHR.PSRC.P5  1960   
4  Homicidios intencionales (por cada 100.000 hab...  VC.IHR.PSRC.P5  1960   

   HomicidiosPor100000     Continente  Población  HomicidiosTotalesAnual  
0                  NaN  North America    54208.0                     NaN  
2                  NaN           Asia  8996967.0                     NaN  
4                  NaN         Africa  5454938.0                     NaN

### Plot6 Tree-map homicidios intencionados por continente

In [ ]:
df = homicidiosIntencionados.query("Año == '2020'")
df.head(3)

Country Name Country Code  \
15960        Aruba          ABW   
15962   Afganistán          AFG   
15964       Angola          AGO   

                                          Indicator Name  Indicator Code  \
15960  Homicidios intencionales (por cada 100.000 hab...  VC.IHR.PSRC.P5   
15962  Homicidios intencionales (por cada 100.000 hab...  VC.IHR.PSRC.P5   
15964  Homicidios intencionales (por cada 100.000 hab...  VC.IHR.PSRC.P5   

        Año  HomicidiosPor100000     Continente   Población  \
15960  2020             1.927228  North America    106766.0   
15962  2020             6.655561           Asia  38928341.0   
15964  2020             4.847075         Africa  32866268.0   

       HomicidiosTotalesAnual  
15960                2.057624  
15962             2590.899541  
15964             1593.052718

interactivo elegir año

In [ ]:
def plotTreemapWidget(year):
  #con query eliges el año o lo que veas, recordar que el año es tipo str en mi dataframe
  year
  df = homicidiosIntencionados.query("Año == '" + year + "'")#query
  df.HomicidiosPor100000.ffill(inplace = True)
  df = df.query("Continente != 'Oceania'")#quito oceania
  fig6 = px.treemap(df, path=[px.Constant('world'), 'Continente', 'Country Name'], values='Población',
                    hover_data=['Country Code'], color='HomicidiosPor100000',
                    labels={
                "HomicidiosPor100000": "Homicidios intencionados (100.000 habts.)",
                "Country Code": "Nombre Abreviado",
                'Año' : '',
                },
                color_continuous_scale='matter',    ) 
  #legend, title
  fig6.update_layout(
      title_text = f'TreeMap, muertes por cada 100000 habitantes para el año {year}',
      showlegend = True,
      )
  #color


  #size
  fig6.update_layout(height=900, margin={"r":10,"t":50,"l":10,"b":10} , width = 1500)
  #fig6.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1000)#si todos iguales descomentar esta linea
  fig6.show()



###Plot 6 widget por año

In [ ]:
widgets.interact(plotTreemapWidget, year = reversed(list(homicidiosIntencionados.Año.unique()[30:]) ) )

interactive(children=(Dropdown(description='year', options=('2021', '2020', '2019', '2018', '2017', '2016', '2…

<function __main__.plotTreemapWidget(year)>

### Plot 6 año 2020 treemap

In [ ]:
#posibles paletas a elegir [ 'orrd', 'matter', 'amp']
#con query eliges el año o lo que veas, recordar que el año es tipo str en mi dataframe
df = homicidiosIntencionados.query("Año == '2020'")
df.HomicidiosPor100000.ffill(inplace = True)
df = df.query("Continente != 'Oceania'")#quito oceania
fig6 = px.treemap(df, path=[px.Constant('world'), 'Continente', 'Country Name'], values='Población',
                    color='HomicidiosPor100000',
                  labels={
              "HomicidiosPor100000": "Homicidios intencionados (100.000 habts.)",
              "Country Code": "",
              'Año' : '',
              'parent':'Continente'
               },
               color_continuous_scale='matter',    ) 
#legend, title
fig6.update_layout(
    title_text = 'TreeMap, muertes por cada 100000 habitantes',
    showlegend = True,
    )
#color


#size
fig6.update_layout(height=900, margin={"r":10,"t":50,"l":10,"b":10} , width = 1500)
fig6.show()


# limpieza de datos de suicidios datosmacro

In [ ]:
#para esta parte es necesario conectarse a mi drive ya que es allí donde tengo el .csv con
# el data scrapping hecho con excel tal y como se enseña en la asignatura

#Update. Ya no, he subido el .xlsx a github para descargar desde allí
#from google.colab import drive
#drive.mount("/content/drive")

Mounted at /content/drive


In [ ]:
import plotly.express as px
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pycountry_convert as pc
import ipywidgets as widgets
import plotly.graph_objects as go
#read several sheets of excel -> https://stackoverflow.com/questions/26521266/using-pandas-to-pd-read-excel-for-multiple-worksheets-of-the-same-workbook


In [ ]:
!wget https://github.com/JavierBescosArtigas/MBID08Visualization-GuidedActies/raw/main/suicidioMundo2020_2006.xlsx
suicidiosDict = pd.ExcelFile('/content/suicidioMundo2020_2006.xlsx')
suicidios2006 = pd.read_excel(suicidiosDict,'2006',  skiprows = 1, header = 0)
suicidios2008 = pd.read_excel(suicidiosDict,'2008', skiprows = 1, header = 0, )
suicidios2010 = pd.read_excel(suicidiosDict, '2010', skiprows = 1, header = 0)#, '2010')
suicidios2012 = pd.read_excel(suicidiosDict, '2012', skiprows = 1, header = 0)#, '2012')
suicidios2014 = pd.read_excel(suicidiosDict, '2014', skiprows = 1, header = 0)#, '2014')
suicidios2016 = pd.read_excel(suicidiosDict, '2016', skiprows = 1, header = 0)#, '2016')
suicidios2018 = pd.read_excel(suicidiosDict, '2018', skiprows = 1, header = 0)#, '2018')
suicidios2020 = pd.read_excel(suicidiosDict, '2020', skiprows = 1, header = 0)#, '2020')
display(suicidios2006.head(3) )
display(suicidios2006.columns )

--2022-11-24 11:22:24--  https://github.com/JavierBescosArtigas/MBID08Visualization-GuidedActies/raw/main/suicidioMundo2020_2006.xlsx
Resolving github.com (github.com)... 140.82.112.4
Connecting to github.com (github.com)|140.82.112.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/JavierBescosArtigas/MBID08Visualization-GuidedActies/main/suicidioMundo2020_2006.xlsx [following]
--2022-11-24 11:22:24--  https://raw.githubusercontent.com/JavierBescosArtigas/MBID08Visualization-GuidedActies/main/suicidioMundo2020_2006.xlsx
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.110.133, 185.199.108.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.110.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 176461 (172K) [application/octet-stream]
Saving to: ‘suicidioMundo2020_2006.xlsx.1’

suicidioMundo2020_2 100%[===================

Unnamed: 0  Unnamed: 1           Países  Fecha  Suicidios mujeres  \
0         NaN         NaN       España [+]   2006                734   
1         NaN         NaN     Alemania [+]   2006               2543   
2         NaN         NaN  Reino Unido [+]   2006                936   

   Suicidios hombres  Suicidios   Suicidios tasa femenina  \
0               2512        3246                     3.29   
1               7231        9774                     6.00   
2               3186        4122                     3.00   

   Suicidios tasa masculina  Suicidios por 100.000    Var.  
0                     11.56                   7.37 -0.0595  
1                     17.90                  11.90 -0.0403  
2                     10.70                   6.80  0.0149

Index(['Unnamed: 0', 'Unnamed: 1', 'Países', 'Fecha', 'Suicidios mujeres',
       'Suicidios hombres', 'Suicidios ', 'Suicidios tasa femenina',
       'Suicidios tasa masculina', 'Suicidios por 100.000', 'Var.'],
      dtype='object')

In [ ]:
#poblacionMundial = poblacionMundial.melt(id_vars = ['Country Name', 'Country Code'],
 #                                        value_name = 'population', var_name = 'Año')
#ffoward por pais
#poblacionMundial['population'] = poblacionMundial.groupby('Country Name')['population'].ffill()


def funcionSucidios(df, anio, toDrop=[]):
  df.Países = df.Países.str.replace('+', '')
  df.Países = df.Países.str.replace(']', '')
  df.Países = df.Países.str.replace('[', '')
  df.Países = df.Países.str.strip()
  df = df.assign(Año = anio)
  for elemento in toDrop:
    try:
      df.drop(columns =elemento, inplace = True)
    except:
      pass
  #print(f'columnas del nuevo dataframe: {df.columns}')
  return df

suicidios2006 = funcionSucidios(suicidios2006, 2006, ['Fecha', 'Var.','Unnamed: 0', 'Unnamed: 1'])
suicidios2008 = funcionSucidios(suicidios2008, 2008, ['Fecha', 'Var.','Unnamed: 0', 'Unnamed: 1'])
suicidios2010 = funcionSucidios(suicidios2010, 2010, ['Fecha', 'Var.','Unnamed: 0', 'Unnamed: 1'])
suicidios2012 = funcionSucidios(suicidios2012, 2012, ['Fecha', 'Var.','Unnamed: 0', 'Unnamed: 1'])
suicidios2014 = funcionSucidios(suicidios2014, 2014, ['Fecha', 'Var.','Unnamed: 0', 'Unnamed: 1'])
suicidios2016 = funcionSucidios(suicidios2016, 2016, ['Fecha', 'Var.','Unnamed: 0', 'Unnamed: 1'])
suicidios2018 = funcionSucidios(suicidios2018, 2018, ['Fecha', 'Var.','Unnamed: 0', 'Unnamed: 1'])
suicidios2020 = funcionSucidios(suicidios2020, 2020, ['Fecha', 'Var.','Unnamed: 0', 'Unnamed: 1'])

#display(suicidios2006.head() )
#display(suicidios2020.head() )

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:8: FutureWarning:

The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:9: FutureWarning:

The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: FutureWarning:

The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.



Países  Suicidios mujeres  Suicidios hombres  Suicidios   \
0       España                734               2512        3246   
1     Alemania               2543               7231        9774   
2  Reino Unido                936               3186        4122   
3      Francia               2866               7744       10610   
4       Italia                859               2842        3701   

   Suicidios tasa femenina  Suicidios tasa masculina  Suicidios por 100.000  \
0                     3.29                     11.56                   7.37   
1                     6.00                     17.90                  11.90   
2                     3.00                     10.70                   6.80   
3                     8.80                     25.20                  16.70   
4                     2.80                      9.90                   6.30   

    Año  
0  2006  
1  2006  
2  2006  
3  2006  
4  2006

Países  Suicidios mujeres  Suicidios hombres  Suicidios   \
0       España               1011               2930        3941   
1     Alemania               2268               7015        9283   
2  Reino Unido               1337               4187        5524   
3      Francia               2091               6298        8389   
4       Italia                824               2901        3725   

   Suicidios tasa femenina  Suicidios tasa masculina  Suicidios por 100.000  \
0                     4.20                     12.60                   8.30   
1                     5.40                     16.90                  11.10   
2                     3.90                     12.60                   8.20   
3                     6.04                     19.45                  12.53   
4                     2.65                      9.78                   6.12   

    Año  
0  2020  
1  2020  
2  2020  
3  2020  
4  2020

### Merge all datasets según paises

In [ ]:
suicidiosEvolucion = pd.concat([suicidios2006, suicidios2008, suicidios2010,
                                suicidios2012, suicidios2014, suicidios2016,
                                suicidios2018, suicidios2020]
                               , axis=0)
suicidiosEvolucion = suicidiosEvolucion.sort_values(['Países', 'Año'])
suicidiosEvolucion.head(10)

Países  Suicidios mujeres  Suicidios hombres  Suicidios   \
10  Afganistán                245               1119        1365   
10  Afganistán                267               1143        1409   
10  Afganistán                293               1147        1440   
10  Afganistán                334               1184        1518   
10  Afganistán                379               1328        1707   
10  Afganistán                401               1395        1796   
10  Afganistán                401               1395        1796   
10  Afganistán                401               1395        1796   
12     Albania                 57                 89         146   
12     Albania                 57                 89         146   

    Suicidios tasa femenina  Suicidios tasa masculina  Suicidios por 100.000  \
10                     1.91                      8.22                   6.32   
10                     1.97                      8.03                   6.13   
10                     2.06                      7.68                   5.93   
10                     2.20                      7.42                   5.87   
10                     2.34                      7.75                   6.18   
10                     2.40                      7.89                   6.32   
10                     2.40                      7.89                   6.32   
10                     2.40                      7.89                   6.32   
12                     3.60                      5.70                   4.70   
12                     3.60                      5.70                   4.70   

     Año  
10  2006  
10  2008  
10  2010  
10  2012  
10  2014  
10  2016  
10  2018  
10  2020  
12  2006  
12  2008

### PLot 7 :Evolucion suicidios

Voy a asignarle un iso-code y un continente a cada país, que en el dataset de **datosmacro** no vienen etiquetados de una manera cómoda para ponerlos en un mapa.

Para ello usaré otro dataset que ya tengo etiquetado, como "diccionario" \{NombrePaísEnEspañol : Continente (: IsoCode)\}

In [ ]:
#AHORA CONTINENTE, UTIL PARA REPRESENTACIONES INTERACTIVAS
suicidiosEvolucion=suicidiosEvolucion.assign(Continente = 1) 
def getContinentsFromName(x):
  #comparing names and continents with pther dataset already labeled
    if len(gastoMilitar [ gastoMilitar['Country Name'] == x ].Continente) != 0:
        return  gastoMilitar [ gastoMilitar['Country Name'] == x ].Continente.unique()[0] #lo ultimo necesario porque hay varias apariciones de España
    else:
        return 'Undetermined'
suicidiosEvolucion.Continente = suicidiosEvolucion["Países"].apply(getContinentsFromName)

#y me quedo con los que han sido etiquetados correctamente
suicidiosEvolucion = suicidiosEvolucion[suicidiosEvolucion.Continente != 'Undetermined']

#AHORA ISO-CODE (util para datawrapper)
suicidiosEvolucion=suicidiosEvolucion.assign(IsoCode = 1) 
def getIsoCodeFromName(x):
  #comparing spanishNames and continents with pther dataset already labeled
    if len(gastoMilitar [ gastoMilitar['Country Name'] == x ]['Country Code']) != 0:
        return  gastoMilitar [ gastoMilitar['Country Name'] == x ]['Country Code'].unique()[0] #lo ultimo necesario porque hay varias apariciones de España
    else:
        return 'Undetermined'
suicidiosEvolucion.IsoCode = suicidiosEvolucion["Países"].apply(getIsoCodeFromName)
#y me quedo con los que han sido etiquetados correctamente
suicidiosEvolucion = suicidiosEvolucion[suicidiosEvolucion.IsoCode != 'Undetermined']

suicidiosEvolucion.head()

Países  Suicidios mujeres  Suicidios hombres  Suicidios   \
10  Afganistán                245               1119        1365   
10  Afganistán                267               1143        1409   
10  Afganistán                293               1147        1440   
10  Afganistán                334               1184        1518   
10  Afganistán                379               1328        1707   

    Suicidios tasa femenina  Suicidios tasa masculina  Suicidios por 100.000  \
10                     1.91                      8.22                   6.32   
10                     1.97                      8.03                   6.13   
10                     2.06                      7.68                   5.93   
10                     2.20                      7.42                   5.87   
10                     2.34                      7.75                   6.18   

     Año Continente IsoCode  
10  2006       Asia     AFG  
10  2008       Asia     AFG  
10  2010       Asia     AFG  
10  2012       Asia     AFG  
10  2014       Asia     AFG

In [ ]:
# pasamos a ver el histórico

##nºPaisesDiferentes en el dataset:
PaisesDif = len(suicidiosEvolucion['Países'].unique())

listaOrdenadaSuicidio = suicidiosEvolucion [suicidiosEvolucion['Año'] == 2020]

listaOrdenadaSuicidio = list(listaOrdenadaSuicidio.nlargest(PaisesDif, ['Suicidios por 100.000'])['Países']) #reutilizando codigo de las secciones anteriores. Funciona


#este diccionario acompañado de la función siguiente nos permitirá etiquetar todos los dataframes para quedarnos con los 15 países más importantes en 2020 ¡pero desde 1960!
dictOrdenDeseado = {}
for i in range(len(listaOrdenadaSuicidio)):
 dictOrdenDeseado[listaOrdenadaSuicidio[i]] = i
#print(dictOrdenDeseado) #obtenidos los paises ordenados segun su indice de suicidio en 2020
def ObtainOrdenDeseado(x):
  try:
    return(dictOrdenDeseado[x])
  except:
    return -1


#Nueva columna con el orden deseado
suicidiosEvolucionOrdenados = suicidiosEvolucion.assign(orden2020 = 0) 
suicidiosEvolucionOrdenados['orden2020'] = suicidiosEvolucionOrdenados['Países'].apply(ObtainOrdenDeseado)#aquí se toman todos los años

#suicidiosEvolucionOrdenados.orden2020.unique() #comprobacion de que se han etiquetado correctametne


In [ ]:
fig7 = px.bar(suicidiosEvolucionOrdenados.sort_values(['orden2020','Países']) ,x="IsoCode",y="Suicidios por 100.000",animation_group="Países",animation_frame="Año" , color="Continente", range_y=[0,35],
              title="Siguiendo el desarrollo histórico de la tasa de suicidio en el mundo.", hover_data=['Países'],
              )
fig7.update_layout(transition = {'duration': 2000})
fig7.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1000)
fig7.show()

In [131]:
suicidiosEvolucion = suicidiosEvolucion.groupby('Países').ffill()
suicidiosEvolucion2020 = suicidiosEvolucion [suicidiosEvolucion.Año == 2020]
suicidiosEvolucion2020.to_csv("suicidiosEvolucion2020.csv")


# Guardar html imágenes y csv tras limpieza para otros usos.


### Imágenes

In [133]:
import plotly
#dimensiones para exportar
altura = 900
anchura = 1800


fig1.update_layout(height=altura, margin={"r":10,"t":50,"l":10,"b":10}, width= anchura)
plotly.offline.plot(fig1, filename = 'fig1.html', auto_open=False)

fig2.update_layout(height=altura, margin={"r":10,"t":50,"l":10,"b":10}, width= anchura)
plotly.offline.plot(fig2, filename = 'fig2.html', auto_open=False)

fig3.update_layout(height=altura, margin={"r":10,"t":50,"l":10,"b":10}, width= anchura)
plotly.offline.plot(fig3, filename = 'fig3.html', auto_open=False)

fig5.update_layout(height=altura, margin={"r":10,"t":50,"l":10,"b":10}, width= anchura)
plotly.offline.plot(fig5, filename = 'fig5.html', auto_open=False)

fig6.update_layout(height=altura, margin={"r":10,"t":50,"l":10,"b":10}, width= anchura)
plotly.offline.plot(fig6, filename = 'fig6.html', auto_open=False)

fig7.update_layout(height=altura, margin={"r":10,"t":50,"l":10,"b":10}, width= anchura)
plotly.offline.plot(fig7, filename = 'fig7.html', auto_open=False)


for scopee in ['africa', 'asia', 'europe', 'north america', 'south america', 'world']:
  proyeccion = 'times'
  if scopee == 'world':
    proyeccion = 'times' #proyeccion ortographic va lageada

  fig4 = go.Figure(go.Choropleth(
        locations = NoTop15absoluto2020['Country Code'],
        locationmode = "ISO-3",
        z = NoTop15absoluto2020['GastoMilitarTotal'],
        text = NoTop15absoluto2020['Country Name'],
        colorscale = 'rainbow',  
      
        reversescale=False,
        marker_line_color='#efefef',
        marker_line_width=0.5,
        
        colorbar_title = 'Gasto Militar (USD)',
        )
    )
  
  # Establecemos las características del título y la apariencia del mapa base
  fig4.update_layout(
      title_text = f'Gasto Militar Absoluto (USD) para el año 2020, ignorando las 15 potencias armamentísticas más influyentes. <br><sup>(Vista {scopee.capitalize()})</sup>',     
      
      showlegend = False,
      geo = dict(
          scope= scopee , #AQUÍ ESTÁ LA MAGIA
          resolution=50,
          #projection_type = 'orthographic',  
          projection_type= proyeccion, # AQUÍ ESTÁ LA MAGIAx2
          showcoastlines=True, coastlinecolor="Black", 
          showocean=True,
          showcountries=True,
          oceancolor="LightBlue",  
          lakecolor="Blue",
          showland=True, landcolor="white",
      )
  )
  fig4.update_layout(height=altura, margin={"r":10,"t":50,"l":10,"b":10}, width= anchura)
  fig4.show()
  plotly.offline.plot(fig4, filename = 'fig4'+scopee+'.html', auto_open=False)


In [135]:
#descomentar si quiero guardar las cosas en mi drive.
#from google.colab import drive
#drive.mount('/content/drive')

#!mkdir HTMLFigurespythonFinal
#!mv ./fig* HTMLFigurespythonFinal/
#!mv HTMLFigurespythonFinal /content/drive/MyDrive/MBID

### Exportar csv asesinatos y suicidios


In [132]:
homicidiosIntencionados2020 = homicidiosIntencionados.ffill()
homicidiosIntencionados2020 = homicidiosIntencionados2020.bfill()
homicidiosIntencionados2020 = homicidiosIntencionados.query("Año == '2020'")

homicidiosIntencionados2000 = homicidiosIntencionados.ffill()
homicidiosIntencionados2000 = homicidiosIntencionados2000.bfill()
homicidiosIntencionados2000 = homicidiosIntencionados.query("Año == '2000'")

homicidiosIntencionados2020.to_csv("homicidiosIntencionados2020.csv")
homicidiosIntencionados2000.to_csv("homicidiosIntencionados2000.csv")

In [ ]:
suicidiosEvolucion2020 = suicidiosEvolucion.groupby('Países').ffill()
suicidiosEvolucion2020 = suicidiosEvolucion.groupby('Países').bfill()
suicidiosEvolucion2020 = suicidiosEvolucion [suicidiosEvolucion.Año == 2020]
suicidiosEvolucion2020.to_csv("suicidiosEvolucion2020.csv")

# Ver las figuras interactivamente, centralizadas desde el cuaderno de colab.

### Fig1, gasto en % del pib

In [ ]:
fig1

### Fig2, gasto USD 

In [ ]:
fig2

### Fig3, evolución histórica del gasto militar de las principales potencias

In [ ]:
fig3

### Fig4, interactiva que no se podía apreciar en el html ó en el pdf

In [130]:
def plotTochoWidget(scopee = 'world', proyeccion = 'times'): #  ['africa', 'asia', 'europe', 'north america', 'south america', 'usa', 'world']
  
  fig4 = go.Figure(go.Choropleth(
      locations = NoTop15absoluto2020['Country Code'],
      locationmode = "ISO-3",
      z = NoTop15absoluto2020['GastoMilitarTotal'],
      text = NoTop15absoluto2020['Country Name'],
      colorscale = 'rainbow',  
    
      reversescale=False,
      marker_line_color='#efefef',
      marker_line_width=0.5,
      
      colorbar_title = 'Gasto Militar (USD)',
      )
  )
  
  # Establecemos las características del título y la apariencia del mapa base
  fig4.update_layout(
      title_text = 'Gasto Militar Absoluto (USD) para el año 2020, ignorando las 15 potencias armamentísticas más influyentes.',
      showlegend = True,
      geo = dict(
          scope= scopee , #AQUÍ ESTÁ LA MAGIA
          resolution=50,
          #projection_type = 'orthographic',  
          projection_type= proyeccion, # AQUÍ ESTÁ LA MAGIAx2
          showcoastlines=True, coastlinecolor="Black", 
          showocean=True,
          showcountries=True,
          oceancolor="LightBlue",  
          lakecolor="Blue",
          showland=True, landcolor="white",
          #tamaño imagen
            )
      )
  
  fig4.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1000)
  
  fig4.show()

#import ipywidgets as widgets
widgets.interact(plotTochoWidget, scopee = ['africa', 'asia', 'europe', 'north america', 'south america', 'world'], proyeccion = ['orthographic', 'times'] )# ['natural earth', 'miller', 'orthographic', 'times', 'airy'])


interactive(children=(Dropdown(description='scopee', index=5, options=('africa', 'asia', 'europe', 'north amer…

<function __main__.plotTochoWidget(scopee='world', proyeccion='times')>

### Fig6, treemap interactivo por año

In [127]:
def plotTreemapWidget(year):
  #con query eliges el año o lo que veas, recordar que el año es tipo str en mi dataframe
  year
  df = homicidiosIntencionados.query("Año == '" + year + "'")#query
  df.HomicidiosPor100000.ffill(inplace = True)
  df = df.query("Continente != 'Oceania'")#quito oceania
  fig6 = px.treemap(df, path=[px.Constant('world'), 'Continente', 'Country Name'], values='Población',
                    hover_data=['Country Code'], color='HomicidiosPor100000',
                    labels={
                "HomicidiosPor100000": "Homicidios intencionados (100.000 habts.)",
                "Country Code": "Nombre Abreviado",
                'Año' : '',
                },
                color_continuous_scale='matter',    ) 
  #legend, title
  fig6.update_layout(
      title_text = f'TreeMap, muertes por cada 100000 habitantes para el año {year}',
      showlegend = True,
      )
  #color


  #size
  fig6.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1200)
  #fig6.update_layout(height=600, margin={"r":10,"t":50,"l":10,"b":10} , width = 1000)#si todos iguales descomentar esta linea
  fig6.show()


In [128]:
widgets.interact(plotTreemapWidget, year = reversed(list(homicidiosIntencionados.Año.unique()[30:]) ) )

interactive(children=(Dropdown(description='year', options=('2021', '2020', '2019', '2018', '2017', '2016', '2…

<function __main__.plotTreemapWidget(year)>

### Fig7, Animación de la tasa de suicidio por continentes

In [ ]:
fig7